In [9]:
!pip install numpy==1.26.4 scipy==1.10.0 easyocr opencv-python pdfplumber python-docx pandas

In [9]:
import os
import cv2
import pdfplumber
import docx
import numpy as np
import easyocr
from PIL import Image

# Инициализация EasyOCR Reader с использованием GPU
reader = easyocr.Reader(['ru'], gpu=True)

def extract_text_from_image(img):
    try:
        # Применяем предобработку к изображению (например, преобразование в серый цвет, бинаризация)
        gray = cv2.cvtColor(img, cv2.COLOR_BGR2GRAY)
        _, binary = cv2.threshold(gray, 150, 255, cv2.THRESH_BINARY + cv2.THRESH_OTSU)

        # Используем EasyOCR для распознавания текста
        results = reader.readtext(binary)

        # Собираем распознанный текст
        text = ' '.join([result[1] for result in results])
        return text
    except Exception as e:
        print(f"Ошибка при обработке изображения: {e}")
        return ""

def extract_text_from_pdf(pdf_path):
    text = ""
    with pdfplumber.open(pdf_path) as pdf:
        for i, page in enumerate(pdf.pages):
            print(f"Обработка страницы {i + 1} из {len(pdf.pages)}")
            
            # Сначала проверяем наличие изображений на странице
            images = page.images
            if images:
                print("Найдены изображения на странице.")
                for j, image in enumerate(images):
                    img_bbox = (image['x0'], image['top'], image['x1'], image['bottom'])
                    # Проверяем, что bbox не выходит за пределы страницы
                    page_bbox = page.bbox
                    if (img_bbox[0] >= page_bbox[0] and img_bbox[1] >= page_bbox[1] and
                        img_bbox[2] <= page_bbox[2] and img_bbox[3] <= page_bbox[3]):
                        print(f"Обработка изображения {j + 1} на странице {i + 1}")
                        
                        try:
                            img = page.within_bbox(img_bbox).to_image()
                            img = img.original

                            # Проверяем, что изображение не пустое
                            if img is not None and img.size != (0, 0):
                                img_np = cv2.cvtColor(np.array(img), cv2.COLOR_RGB2BGR)
                                img_text = extract_text_from_image(img_np)
                                
                                if img_text:
                                    # Выводим первые 100 символов считанного текста с изображения
                                    print(f"Считанный текст с изображения: {img_text[:100]}")
                                    text += img_text + "\n"
                                else:
                                    print("Текст не найден на изображении.")
                            else:
                                print("Изображение пустое или не было загружено.")
                        except Exception as e:
                            print(f"Ошибка при обработке изображения на странице {i + 1}: {e}")

            # Затем проверяем наличие текста на странице
            try:
                page_text = page.extract_text()
                if page_text:
                    print("Найдены текстовые данные на странице.")
                    # Выводим первые 100 символов текста со страницы
                    print(f"Считанный текст со страницы: {page_text[:100]}")
                    text += page_text + "\n"
                else:
                    print("Текст не найден на странице.")
            except Exception as e:
                print(f"Ошибка при извлечении текста со страницы {i + 1}: {e}")

    return text

def extract_text_from_docx(docx_path):
    text = ""
    doc = docx.Document(docx_path)
    
    # Извлечение текста из параграфов
    for para in doc.paragraphs:
        text += para.text + "\n"
        print(f"Считанный текст со страницы: {text[:100]}")
    
    # Обработка изображений в документе
    for i, shape in enumerate(doc.inline_shapes):
        if shape.type == 3:  # Проверяем, является ли это изображением
            print(f"Обработка изображения {i + 1} из {len(doc.inline_shapes)} в {docx_path}")
            try:
                image = shape._inline.graphic.graphicData.pic.blipFill.blip.embed
                image_part = doc.part.related_parts[image]
                img = Image.open(image_part.blob)
                img_np = cv2.cvtColor(np.array(img), cv2.COLOR_RGB2BGR)
                img_text = extract_text_from_image(img_np)
                if img_text:
                    # Выводим первые 100 символов считанного текста с изображения
                    print(f"Считанный текст с изображения в DOCX: {img_text[:100]}")
                    text += img_text + "\n"
                else:
                    print("Текст не найден на изображении в DOCX.")
            except Exception as e:
                print(f"Ошибка при обработке изображения в DOCX: {e}")

    return text

def extract_text_from_files(directory):
    texts = {}
    files = os.listdir(directory)
    total_files = len(files)  # Общее количество файлов
    processed_files = 0  # Счетчик обработанных файлов
    
    for filename in files:
        try:
            if filename.endswith(".pdf"):
                pdf_path = os.path.join(directory, filename)
                print(f"Обработка PDF: {filename}")
                texts[filename] = extract_text_from_pdf(pdf_path)
            elif filename.endswith(".docx"):
                docx_path = os.path.join(directory, filename)
                print(f"Обработка DOCX: {filename}")
                texts[filename] = extract_text_from_docx(docx_path)
            processed_files += 1  # Увеличиваем счетчик обработанных файлов
            
            # Выводим информацию о прогрессе
            remaining_files = total_files - processed_files
            print(f"\n---\nОсталось {remaining_files} файлов из {total_files}\n---\n")
            
        except Exception as e:
            print(e)
    return texts


In [10]:

directory = 'documents/'
extracted_texts = extract_text_from_files(directory)


Обработка DOCX: 4 ОВАЛ - Инвентаризация.docx
Считанный текст со страницы: 

Считанный текст со страницы: 


Считанный текст со страницы: 



Считанный текст со страницы: 




Считанный текст со страницы: 





Считанный текст со страницы: 




ОТЧЕТ ПО

Считанный текст со страницы: 




ОТЧЕТ ПО
ИНВЕНТАРИЗАЦИИ СТАЦИОНАРНЫХ ИСТОЧНИКОВ И ВЫБРОСОВ ЗАГРЯЗНЯЮЩИХ ВЕЩЕСТВ В АТМОСФЕРНЫЙ В
Считанный текст со страницы: 




ОТЧЕТ ПО
ИНВЕНТАРИЗАЦИИ СТАЦИОНАРНЫХ ИСТОЧНИКОВ И ВЫБРОСОВ ЗАГРЯЗНЯЮЩИХ ВЕЩЕСТВ В АТМОСФЕРНЫЙ В
Считанный текст со страницы: 




ОТЧЕТ ПО
ИНВЕНТАРИЗАЦИИ СТАЦИОНАРНЫХ ИСТОЧНИКОВ И ВЫБРОСОВ ЗАГРЯЗНЯЮЩИХ ВЕЩЕСТВ В АТМОСФЕРНЫЙ В
Считанный текст со страницы: 




ОТЧЕТ ПО
ИНВЕНТАРИЗАЦИИ СТАЦИОНАРНЫХ ИСТОЧНИКОВ И ВЫБРОСОВ ЗАГРЯЗНЯЮЩИХ ВЕЩЕСТВ В АТМОСФЕРНЫЙ В
Считанный текст со страницы: 




ОТЧЕТ ПО
ИНВЕНТАРИЗАЦИИ СТАЦИОНАРНЫХ ИСТОЧНИКОВ И ВЫБРОСОВ ЗАГРЯЗНЯЮЩИХ ВЕЩЕСТВ В АТМОСФЕРНЫЙ В
Считанный текст со страницы: 




ОТЧЕТ ПО
ИНВЕНТАРИЗАЦИИ СТАЦИОНАРНЫХ ИСТОЧНИКОВ И ВЫБРОСОВ ЗАГ

In [ ]:
import pandas as pd
from transformers import RobertaTokenizer, RobertaForQuestionAnswering, Trainer, TrainingArguments
from datasets import Dataset
from sklearn.model_selection import train_test_split

# Загрузка данных
train_df = pd.read_csv('train.csv')

# Функция для подготовки данных
def prepare_data(df):
    contexts = df['Ответ'].tolist()
    questions = df['Вопрос'].tolist()
    
    start_positions = []
    end_positions = []
    
    for index, row in df.iterrows():
        answer = row['Ответ']
        start_idx = contexts[df.index.get_loc(index)].find(answer)  # Начало ответа
        end_idx = start_idx + len(answer) - 1  # Конец ответа
        start_positions.append(start_idx)
        end_positions.append(end_idx)

    return contexts, questions, start_positions, end_positions

# Подготовка данных
contexts, questions, start_positions, end_positions = prepare_data(train_df)

# Инициализация токенизатора и модели
tokenizer = RobertaTokenizer.from_pretrained("roberta-base")
model = RobertaForQuestionAnswering.from_pretrained("roberta-base")

# Функция токенизации
def tokenize_data(contexts, questions):
    encodings = tokenizer(contexts, questions, truncation=True, padding=True, max_length=512)
    return encodings

# Токенизация данных
encodings = tokenize_data(contexts, questions)

# Создание Dataset для обучения
dataset = Dataset.from_dict({
    'input_ids': encodings['input_ids'],
    'attention_mask': encodings['attention_mask'],
    'start_positions': start_positions,
    'end_positions': end_positions
})

# Создание валидационного набора данных
train_df, val_df = train_test_split(train_df, test_size=0.2, random_state=42)

# Подготовка данных для валидации
contexts_val, questions_val, start_positions_val, end_positions_val = prepare_data(val_df)

# Токенизация данных для валидации
encodings_val = tokenize_data(contexts_val, questions_val)

# Создание Dataset для валидации
val_dataset = Dataset.from_dict({
    'input_ids': encodings_val['input_ids'],
    'attention_mask': encodings_val['attention_mask'],
    'start_positions': start_positions_val,
    'end_positions': end_positions_val
})

# Определение аргументов для обучения
training_args = TrainingArguments(
    output_dir='./results',
    eval_strategy='epoch',
    num_train_epochs=8000,
    per_device_train_batch_size=8,
    per_device_eval_batch_size=8,
    learning_rate=5e-5,
    logging_dir='./logs',
    logging_steps=10,
)

# Определение тренера
trainer = Trainer(
    model=model,
    args=training_args,
    train_dataset=dataset,
    eval_dataset=val_dataset
)

# Запуск обучения
trainer.train()

# Сохранение модели и токенизатора
trainer.save_model('./results')
tokenizer.save_pretrained('./results')


Some weights of RobertaForQuestionAnswering were not initialized from the model checkpoint at roberta-base and are newly initialized: ['qa_outputs.bias', 'qa_outputs.weight']
You should probably TRAIN this model on a down-stream task to be able to use it for predictions and inference.
Be aware, overflowing tokens are not returned for the setting you have chosen, i.e. sequence pairs with the 'longest_first' truncation strategy. So the returned list will always be empty even if some tokens have been removed.
Be aware, overflowing tokens are not returned for the setting you have chosen, i.e. sequence pairs with the 'longest_first' truncation strategy. So the returned list will always be empty even if some tokens have been removed.
Be aware, overflowing tokens are not returned for the setting you have chosen, i.e. sequence pairs with the 'longest_first' truncation strategy. So the returned list will always be empty even if some tokens have been removed.
Be aware, overflowing tokens are not

In [2]:
import torch
from transformers import RobertaTokenizer, RobertaForQuestionAnswering

# Загрузка токенизатора и модели
tokenizer = RobertaTokenizer.from_pretrained("./results")
model = RobertaForQuestionAnswering.from_pretrained("./results")

# Ваш вопрос
question = "Каковы источники выбросов загрязняющих веществ от авторемонтной мастерской?"

# Контекст
context = """
Для определения показателей выбросов организованных ИЗАВ используются преимущественно инструментальные методы. 
Случаи, при которых допускается использование расчетных методов для определения качественного и количественного состава выбросов из выявленных ИЗАВ, указаны в пунктах 26-28 настоящего Порядка. 
В случае использования расчетных методов в отчет о результатах инвентаризации выбросов, предусмотренный главой V настоящего Порядка, включается обоснование выбора и применения использованных методов.
Для определения показателей выбросов от передвижных ИЗАВ используются преимущественно расчетные методы.
Использование расчетных методов для определения показателей выбросов организованных ИЗАВ допускается в следующих случаях:
отсутствие аттестованных методик (методов) измерения загрязняющего вещества;
отсутствие практической возможности забора проб для определения инструментальными методами в соответствии с национальными стандартами Российской Федерации, утверждаемыми Росстандартом в соответствии с требованиями законодательства Российской Федерации об обеспечении единства измерений;
отсутствие практической возможности проведения инструментальных измерений выбросов (например, высокая температура газовоздушной смеси, высокая скорость потока отходящих газов, сверхнизкое или сверхвысокое давление внутри газохода, отсутствие доступа к ИЗАВ).
"""

# Токенизация входных данных
inputs = tokenizer(question, context, return_tensors="pt", truncation=True, padding=True, max_length=512)

# Получение ответов
with torch.no_grad():
    outputs = model(**inputs)

# Получение индексов начала и конца ответа
start_logits = outputs.start_logits
end_logits = outputs.end_logits

# Применение softmax для получения вероятностей
start_probs = torch.softmax(start_logits, dim=-1)
end_probs = torch.softmax(end_logits, dim=-1)

# Индексы ответа
start_index = torch.argmax(start_probs)
end_index = torch.argmax(end_probs)

# Корректировка индексов
if start_index >= end_index:
    answer = "Ответ не найден, проверьте контекст и вопрос."
else:
    # Декодирование ответа
    answer_tokens = inputs['input_ids'][0][start_index:end_index + 100]  # включаем end_index
    answer = tokenizer.decode(answer_tokens)

print(f"Вопрос: {question}")
print(f"Ответ: {answer}")


Be aware, overflowing tokens are not returned for the setting you have chosen, i.e. sequence pairs with the 'longest_first' truncation strategy. So the returned list will always be empty even if some tokens have been removed.


Вопрос: Каковы источники выбросов загрязняющих веществ от авторемонтной мастерской?
Ответ: <s>Каковы источники выбросов загрязняющих веществ от авторемонтной мастерской?</s></s>
Для определения показателей выбросов организованных ИЗАВ используются преимущественно инструментальные методы. 
Случаи, при которых допускается использование расчетных методов для определения качественного и количественного состава выбросов из выявленных ИЗАВ, указаны в пунктах 26-28 настоящего Порядка. 
В случае использования расчетных методов в отчет о результатах инвентариза�</s>


In [75]:
os.system('ls')

NameError: name 'os' is not defined

In [1]:
!pip install sentencepiece

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 1.3/1.3 MB 10.8 MB/s eta 0:00:0000:010:01
